# Análisis Geoespacial de Colonias de Hermosillo

Este notebook explora y visualiza los polígonos de colonias (neighborhoods) de Hermosillo usando datos del shapefile INE_Limpio.

**Objetivos:**
- Cargar datos geoespaciales de colonias de Sonora
- Filtrar solo las colonias de Hermosillo
- Crear visualización interactiva con Folium
- Exportar datos procesados

**Total de colonias de Hermosillo: 700** (incluyendo MultiPolygons)

## 1. Importar librerías necesarias

In [51]:
import os
import geopandas as gpd
import pandas as pd
import requests
import folium
from shapely.ops import unary_union
from pathlib import Path

print("✅ Librerías cargadas correctamente")

✅ Librerías cargadas correctamente


## 2. Descargar y cargar datos del shapefile

In [52]:
# Configuración de rutas
datos_dir = Path('..') / 'data' / 'raw'
datos_dir.mkdir(parents=True, exist_ok=True)

# URLs del repositorio de Luis Moreno
repo_url = "https://github.com/Sonora-en-Datos/ColoniasSonora/raw/main/shapes/INE_Limpio/"
files = ["INE_Limpio.shp", "INE_Limpio.dbf", "INE_Limpio.shx", "INE_Limpio.prj"]

print("📥 Descargando archivos del shapefile...")
for fname in files:
    try:
        response = requests.get(repo_url + fname, timeout=10)
        if response.status_code == 200:
            filepath = datos_dir / fname
            with open(filepath, "wb") as f:
                f.write(response.content)
            print(f"  ✓ {fname}")
    except Exception as e:
        print(f"  ❌ Error descargando {fname}: {e}")

print("\n📂 Cargando datos geoespaciales...")
shapefile_path = datos_dir / "INE_Limpio.shp"
gdf_completo = gpd.read_file(shapefile_path)
print(f"  Total de registros: {len(gdf_completo)}")
print(f"  CRS: {gdf_completo.crs}")

📥 Descargando archivos del shapefile...
  ✓ INE_Limpio.shp
  ✓ INE_Limpio.dbf
  ✓ INE_Limpio.shx
  ✓ INE_Limpio.prj

📂 Cargando datos geoespaciales...
  Total de registros: 2622
  CRS: GEOGCS["GCS_WGS_84_CRS84",DATUM["WGS_1984",SPHEROID["WGS 84",6378137,298.257223563,AUTHORITY["EPSG","7030"]],AUTHORITY["EPSG","6326"]],PRIMEM["Greenwich",0],UNIT["Degree",0.0174532925199433],AXIS["Longitude",EAST],AXIS["Latitude",NORTH]]


## 3. Filtrar geometrías válidas

In [53]:
print("🔍 Filtrando geometrías válidas...\n")

# Mostrar tipos de geometría disponibles
print("Tipos de geometría en INE_Limpio.shp:")
print(gdf_completo.geometry.type.value_counts())

# Incluir Polygon Y MultiPolygon (los MultiPolygons son colonias con áreas discontinuas)
gdf_poligonos = gdf_completo[gdf_completo.geometry.type.isin(['Polygon', 'MultiPolygon'])].copy()

print(f"\n✅ Polígonos válidos extraídos: {len(gdf_poligonos)} de {len(gdf_completo)}")

🔍 Filtrando geometrías válidas...

Tipos de geometría en INE_Limpio.shp:
Polygon         2581
MultiPolygon      41
Name: count, dtype: int64

✅ Polígonos válidos extraídos: 2622 de 2622


## 4. Filtrar colonias de Hermosillo

In [54]:
print("🏘️  Filtrando colonias de Hermosillo...\n")

# Filtrar por localidad
gdf_hermosillo = gdf_poligonos[gdf_poligonos['nom_loc'] == 'Hermosillo'].copy()

print(f"Total de colonias de Hermosillo: {len(gdf_hermosillo)}")
print(f"Colonias únicas: {gdf_hermosillo['nom_col'].nunique()}")
print(f"\nColumnas disponibles: {list(gdf_hermosillo.columns)}")

🏘️  Filtrando colonias de Hermosillo...

Total de colonias de Hermosillo: 700
Colonias únicas: 700

Columnas disponibles: ['cve_ent', 'cve_mun', 'cve_loc', 'nom_loc', 'cve_col', 'nom_col', 'cp', 'otros_cp', 'geometry']


## 5. Análisis de tipos de geometría

In [55]:
print("📊 Análisis de geometrías en Hermosillo:\n")

# Contar tipos de geometría
geometry_counts = gdf_hermosillo.geometry.type.value_counts()
print("Tipos de geometría:")
for geom_type, count in geometry_counts.items():
    print(f"  • {geom_type}: {count}")

# Colonias con MultiPolygon (áreas discontinuas)
multipolygons = gdf_hermosillo[gdf_hermosillo.geometry.type == 'MultiPolygon']
if len(multipolygons) > 0:
    print(f"\n🔷 Colonias con áreas discontinuas (MultiPolygon): {len(multipolygons)}")
    print("\nEjemplos:")
    for idx, (_, row) in enumerate(multipolygons.head(10).iterrows()):
        print(f"  {idx+1}. {row['nom_col']} (CVE: {row['cve_col']})")

📊 Análisis de geometrías en Hermosillo:

Tipos de geometría:
  • Polygon: 680
  • MultiPolygon: 20

🔷 Colonias con áreas discontinuas (MultiPolygon): 20

Ejemplos:
  1. SAN MARCOS (CVE: 2603000012361)
  2. ALTARES (CVE: 2603000011589)
  3. SAHUARO (CVE: 2603000011766)
  4. LOS ALAMOS (CVE: 2603000011670)
  5. ALVARO OBREGON (CVE: 2603000011867)
  6. VILLAS DEL SUR (CVE: 2603000012196)
  7. VILLA COLONIAL (CVE: 2603000011372)
  8. LAS PALMAS (CVE: 2603000011494)
  9. SAN LORENZO (CVE: 2603000011506)
  10. LIRIOS (CVE: 2603000011624)


## 6. Exportar datos procesados

In [56]:
print("💾 Exportando datos...\n")

# Exportar a CSV
csv_path = datos_dir / 'poligonos_hermosillo.csv'
gdf_hermosillo.to_csv(csv_path, index=False, encoding='utf-8-sig')
print(f"✓ CSV guardado: {csv_path.name}")

# Exportar a Shapefile
shp_path = datos_dir / 'poligonos.shp'
gdf_poligonos.to_file(shp_path)
print(f"✓ Shapefile guardado: poligonos.shp")

print(f"\n📍 Total de registros exportados: {len(gdf_hermosillo)}")

💾 Exportando datos...

✓ CSV guardado: poligonos_hermosillo.csv
✓ Shapefile guardado: poligonos.shp

📍 Total de registros exportados: 700


## 7. Crear mapa interactivo

In [57]:
print("🗺️  Creando mapa interactivo...\n")

# Calcular centroide de Hermosillo
centro = unary_union(gdf_hermosillo.geometry).centroid
print(f"📍 Centro: Lat {centro.y:.4f}, Lon {centro.x:.4f}")

# Crear mapa base
m = folium.Map(
    location=[centro.y, centro.x],
    zoom_start=11,
    tiles='OpenStreetMap'
)

# Agregar polígonos al mapa
for idx, row in gdf_hermosillo.iterrows():
    # Estilo diferente para MultiPolygons
    is_multipolygon = row['geometry'].type == 'MultiPolygon'
    color = '#e63c31' if is_multipolygon else '#08519c'
    
    popup_text = f"""
    <b>{row['nom_col']}</b><br>
    <small>
    CVE: {row['cve_col']}<br>
    CP: {row['cp']}<br>
    {"🔷 Área discontinua" if is_multipolygon else ""}
    </small>
    """
    
    folium.GeoJson(
        row['geometry'].__geo_interface__,
        style_function=lambda x, color=color: {
            'fillColor': color,
            'color': '#000000',
            'weight': 1,
            'fillOpacity': 0.5 if is_multipolygon else 0.4
        },
        popup=folium.Popup(popup_text, max_width=300),
        tooltip=row['nom_col']
    ).add_to(m)

# Agregar controles
folium.LayerControl(position='topright', collapsed=False).add_to(m)

print(f"✅ Mapa creado con {len(gdf_hermosillo)} colonias")
print(f"   • Azul: colonias regulares (Polygon)")
print(f"   • Rojo: colonias con áreas discontinuas (MultiPolygon)")

# Mostrar mapa
m

🗺️  Creando mapa interactivo...

📍 Centro: Lat 29.0854, Lon -110.9775


C:\Users\marce\AppData\Local\Temp\ipykernel_27272\164260283.py:17: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  is_multipolygon = row['geometry'].type == 'MultiPolygon'


✅ Mapa creado con 700 colonias
   • Azul: colonias regulares (Polygon)
   • Rojo: colonias con áreas discontinuas (MultiPolygon)


## 8. Guardar mapa como archivo HTML

In [58]:
# Guardar mapa
map_path = Path('../mapa_colonias_hermosillo.html')
m.save(str(map_path))

print(f"✅ Mapa guardado: {map_path}")
print(f"📊 Resumen:")
print(f"   • Total de colonias visualizadas: {len(gdf_hermosillo)}")
print(f"   • Polígonos regulares: {len(gdf_hermosillo[gdf_hermosillo.geometry.type == 'Polygon'])}")
print(f"   • MultiPolygons: {len(gdf_hermosillo[gdf_hermosillo.geometry.type == 'MultiPolygon'])}")

✅ Mapa guardado: ..\mapa_colonias_hermosillo.html
📊 Resumen:
   • Total de colonias visualizadas: 700
   • Polígonos regulares: 680
   • MultiPolygons: 20


## 9. Tabla de resumen de colonias

In [59]:
# Crear tabla de resumen
df_resumen = gdf_hermosillo[['cve_col', 'nom_col', 'cp']].copy()
df_resumen['geometry_type'] = gdf_hermosillo.geometry.type.values
df_resumen = df_resumen.sort_values('nom_col')

print(f"📋 Primeras 20 colonias de Hermosillo:\n")
print(df_resumen.head(20).to_string(index=False))
print(f"\n... (y {len(df_resumen) - 20} más)")

📋 Primeras 20 colonias de Hermosillo:

      cve_col                        nom_col      cp geometry_type
2603000012052                    14 DE MARZO 83287.0       Polygon
2603000016288                     4 DE MARZO 83105.0       Polygon
2603000011947               4TA ZONA MILITAR 83150.0       Polygon
2603000016473            ACACIAS RESIDENCIAL 83177.0       Polygon
2603000011671            ADOLFO DE LA HUERTA 83295.0       Polygon
2603000011459            ADOLFO LOPEZ MATEOS 83170.0       Polygon
2603000011646    ADOLFO LOPEZ MATEOS ETAPA I 83140.0       Polygon
2603000012021             AGAVES RESIDENCIAL 83140.0       Polygon
2603000011674                        AKIWIKI 83290.0       Polygon
2603000011457                        ALAMEDA 83200.0       Polygon
2603000016447          ALEGRANZA RESIDENCIAL 83287.0       Polygon
2603000011640                ALFONSO PERALTA 83140.0       Polygon
2603000016497           ALONDRAS RESIDENCIAL 83105.0       Polygon
2603000011846    ALTA C

In [60]:
import pandas as pd

In [61]:
import os
import geopandas as gpd
import requests

# URL base del repositorio de luis Moreno
repo_url = "https://github.com/Sonora-en-Datos/ColoniasSonora/raw/main/shapes/INE_Limpio/"
files = [
    "INE_Limpio.shp", "INE_Limpio.dbf", "INE_Limpio.shx", "INE_Limpio.prj"
]
datos_dir =  r"..\data\raw"
os.makedirs(datos_dir, exist_ok=True)

# Descarga de archivos
for fname in files:
    r = requests.get(repo_url + fname)
    with open(os.path.join(datos_dir, fname), "wb") as f:
        f.write(r.content)
    print(f"Descargado: {fname}")

# Leer shapefile y sacar polígonos
shapefile_path = os.path.join(datos_dir, "INE_Limpio.shp")
gdf = gpd.read_file(shapefile_path)

# CORRECCIÓN: Incluir TODOS los polígonos (Polygon Y MultiPolygon)
# Las colonias pueden tener geometrías MultiPolygon (áreas discontinuas)
poligonos = gdf[gdf.geometry.type.isin(['Polygon', 'MultiPolygon'])]

# Muestra o guarda los datos filtrados
print(f"\n✓ Total de polígonos extraídos: {len(poligonos)} (de {len(gdf)} registros)")
print(poligonos.head())
poligonos.to_file(os.path.join(datos_dir, "poligonos.shp"))

Descargado: INE_Limpio.shp
Descargado: INE_Limpio.dbf
Descargado: INE_Limpio.dbf
Descargado: INE_Limpio.shx
Descargado: INE_Limpio.shx
Descargado: INE_Limpio.prj

✓ Total de polígonos extraídos: 2622 (de 2622 registros)
  cve_ent cve_mun cve_loc            nom_loc        cve_col  \
0      26     043    0001    Heroica Nogales  2604300011317   
1      26     036    0001  Magdalena de Kino   260360001128   
2      26     029    0001    Heroica Guaymas     2602900019   
3      26     030    0001         Hermosillo  2603000016735   
4      26     029    0001    Heroica Guaymas   260290001207   

                          nom_col       cp otros_cp  \
0                 VILLA GUADALUPE  84064.0     None   
1                       LA ANTENA  84160.0     None   
2                        SAN JOSE  85460.0     None   
3  ALTA FIRENZE NORTE RESIDENCIAL  83104.0     None   
4                      LAS PALMAS  85470.0     None   

                                            geometry  
0  POLYGON ((-1

In [62]:
poligonos.head()

cve_ent cve_mun cve_loc            nom_loc        cve_col  \
0      26     043    0001    Heroica Nogales  2604300011317   
1      26     036    0001  Magdalena de Kino   260360001128   
2      26     029    0001    Heroica Guaymas     2602900019   
3      26     030    0001         Hermosillo  2603000016735   
4      26     029    0001    Heroica Guaymas   260290001207   

                          nom_col       cp otros_cp  \
0                 VILLA GUADALUPE  84064.0     None   
1                       LA ANTENA  84160.0     None   
2                        SAN JOSE  85460.0     None   
3  ALTA FIRENZE NORTE RESIDENCIAL  83104.0     None   
4                      LAS PALMAS  85470.0     None   

                                            geometry  
0  POLYGON ((-110.95786 31.29394, -110.95783 31.2...  
1  POLYGON ((-110.95489 30.64, -110.95472 30.6402...  
2  POLYGON ((-110.90281 27.91273, -110.90269 27.9...  
3  POLYGON ((-110.95631 29.14264, -110.95576 29.1...  
4  POLYGON ((-110.91774 27.89986, -110.91724 27.9...

In [63]:
# colonias de hermosillo 
colonia_hermosillo = poligonos[poligonos['nom_loc'] == 'Hermosillo']
colonia_hermosillo


cve_ent cve_mun cve_loc     nom_loc        cve_col  \
3         26     030    0001  Hermosillo  2603000016735   
7         26     030    0001  Hermosillo  2603000011785   
12        26     030    0001  Hermosillo  2603000016335   
16        26     030    0001  Hermosillo  2603000011480   
25        26     030    0001  Hermosillo  2603000011663   
...      ...     ...     ...         ...            ...   
2605      26     030    0001  Hermosillo  2603000011353   
2606      26     030    0001  Hermosillo  2603000011416   
2611      26     030    0001  Hermosillo  2603000011649   
2613      26     030    0001  Hermosillo  2603000011852   
2616      26     030    0001  Hermosillo  2603000011647   

                              nom_col       cp otros_cp  \
3      ALTA FIRENZE NORTE RESIDENCIAL  83104.0     None   
7                 JORGE VALDEZ MUÃOZ  83104.0     None   
12    VILLA VERDE CERRADA SAN VICENTE  83118.0     None   
16                      VILLA VENTURA  83159.0     None   
25                   NUEVO HERMOSILLO  83296.0     None   
...                               ...      ...      ...   
2605                       EL ENCANTO  83105.0     None   
2606                        PRIMAVERA  83113.0     None   
2611                    COSTA DEL SOL  83140.0     None   
2613                   VISTA DEL LAGO  83240.0     None   
2616                       CASA LINDA  83140.0     None   

                                               geometry  
3     POLYGON ((-110.95631 29.14264, -110.95576 29.1...  
7     POLYGON ((-111.02777 29.14465, -111.02736 29.1...  
12    POLYGON ((-111.02279 29.16803, -111.02213 29.1...  
16    POLYGON ((-110.93927 29.10724, -110.9389 29.10...  
25    POLYGON ((-110.93549 29.02284, -110.93543 29.0...  
...                                                 ...  
2605  POLYGON ((-110.99857 29.1482, -110.99823 29.14...  
2606  POLYGON ((-110.98806 29.13114, -110.98748 29.1...  
2611  POLYGON ((-110.96176 29.02565, -110.96142 29.0...  
2613  POLYGON ((-110.99888 29.0771, -110.99734 29.07...  
2616  POLYGON ((-110.96723 29.02663, -110.96719 29.0...  

[700 rows x 9 columns]

In [64]:
# Verificar cuántos polígonos tenemos en cada paso
print(f"Total de registros en INE_Limpio.shp: {len(gdf)}")
print(f"Total de polígonos (después de filtrar por geometry.type == 'Polygon'): {len(poligonos)}")
print(f"Total de colonias de Hermosillo: {len(colonia_hermosillo)}")
print(f"\nColonias únicas en Hermosillo: {colonia_hermosillo['nom_col'].nunique()}")
print(f"\nTipos de geometría en INE_Limpio original:")
print(gdf.geometry.type.value_counts())

Total de registros en INE_Limpio.shp: 2622
Total de polígonos (después de filtrar por geometry.type == 'Polygon'): 2622
Total de colonias de Hermosillo: 700

Colonias únicas en Hermosillo: 700

Tipos de geometría en INE_Limpio original:
Polygon         2581
MultiPolygon      41
Name: count, dtype: int64


In [65]:
# guardamos en csv las colonias hermosillo en un csv 
output_csv_path_hermosillo = os.path.join(datos_dir, 'poligonos_hermosillo.csv')
colonia_hermosillo.to_csv(output_csv_path_hermosillo, index=False, encoding='utf-8-sig')
print(f"\n¡Éxito! Archivo guardado en: {output_csv_path_hermosillo}")


¡Éxito! Archivo guardado en: ..\data\raw\poligonos_hermosillo.csv


In [66]:
# Verificar las 20 colonias que se estaban perdiendo antes
multipolygons_hmo = colonia_hermosillo[colonia_hermosillo.geometry.type == 'MultiPolygon']
print(f"\n📊 Colonias con geometría MultiPolygon en Hermosillo: {len(multipolygons_hmo)}")
print("\n🏘️ Ejemplos de colonias recuperadas (tenían áreas discontinuas):")
print(multipolygons_hmo[['cve_col', 'nom_col']].head(10))


📊 Colonias con geometría MultiPolygon en Hermosillo: 20

🏘️ Ejemplos de colonias recuperadas (tenían áreas discontinuas):
            cve_col         nom_col
331   2603000012361      SAN MARCOS
434   2603000011589         ALTARES
628   2603000011766         SAHUARO
669   2603000011670      LOS ALAMOS
746   2603000011867  ALVARO OBREGON
767   2603000012196  VILLAS DEL SUR
872   2603000011372  VILLA COLONIAL
961   2603000011494      LAS PALMAS
1091  2603000011506     SAN LORENZO
1111  2603000011624          LIRIOS


In [67]:
import folium
from shapely.ops import unary_union

# Calcular el centroide usando el método moderno
centro = unary_union(colonia_hermosillo.geometry).centroid
print(f"📍 Centro de Hermosillo: ({centro.y:.4f}, {centro.x:.4f})")

# Crear el mapa
m = folium.Map(location=[centro.y, centro.x], zoom_start=11, tiles='OpenStreetMap')

# Agregar los polígonos al mapa
for idx, row in colonia_hermosillo.iterrows():
    folium.GeoJson(
        row['geometry'].__geo_interface__,
        style_function=lambda x: {
            'fillColor': '#08519c',
            'color': '#000000',
            'weight': 1,
            'fillOpacity': 0.4
        },
        popup=folium.Popup(f"<b>{row['nom_col']}</b><br>CP: {row['cp']}", max_width=300),
        tooltip=row['nom_col']
    ).add_to(m)

# Agregar controles
folium.LayerControl().add_to(m)

# Mostrar el mapa
m

📍 Centro de Hermosillo: (29.0854, -110.9775)
